In [1]:
import spacy
from spacy.matcher import Matcher
import pandas as pd
from tqdm import tqdm
import networkx as nx
import re
import matplotlib.pyplot as plt
import joblib

In [2]:
def load_file(file_path):
    with open(file_path, 'r', encoding='utf-8') as file:
        text = file.read()
    text = re.sub(r'\[\d+\]', '', text)
    
    text = re.sub(r'[^\w\s.,]', '', text)
    
    text = re.sub(r'\s+', ' ', text).strip()
    return text

file_path = r"c:\Users\sravan\OneDrive\Documents\cyber security file.txt"
paragraph_text = load_file(file_path)

In [3]:
nlp = spacy.load('en_core_web_lg')
doc = nlp(paragraph_text)

data = []
for sent in doc.sents:
    data.append(sent.text)

In [ ]:
data

['A cyberattack or cyber attack occurs when there is an unauthorized action against computer infrastructure that compromises the confidentiality, integrity, or availability of its content.',
 'The rising dependence on increasingly complex and interconnected computer systems in most domains of life is the main factor that causes vulnerability to cyberattacks, since virtually all computer systems have bugs that can be exploited by attackers.',
 'Although it is impossible or impractical to create a perfectly secure system, there are many defense mechanisms that can make a system more difficult to attack.',
 'Perpetrators of a cyberattack can be criminals, hacktivists, or states.',
 'They attempt to find weaknesses in a system, exploit them and create malware to carry out their goals, and deliver it to the targeted system.',
 'Once installed, the malware can have a variety of effects depending on its purpose.',
 'Detection of cyberattacks is often absent or delayed, especially when the mal

In [ ]:
df = pd.DataFrame(data)
df.columns = ['sentences']
df

sentences
0    A cyberattack or cyber attack occurs when ther...
1    The rising dependence on increasingly complex ...
2    Although it is impossible or impractical to cr...
3    Perpetrators of a cyberattack can be criminals...
4    They attempt to find weaknesses in a system, e...
..                                                 ...
144  International courts cannot enforce these laws...
145  In many countries, cyberattacks are prosecutab...
146  Attribution of the attack beyond reasonable do...
147  In 2021, United Nations member states began ne...
148  Many jurisdictions have data breach notificati...

[149 rows x 1 columns]

In [6]:
doc=nlp("Snort is used for signature based intrusion detection ")

In [7]:
for tok in doc:
    print(tok.text, "-->", tok.dep_)

Snort --> nsubjpass
is --> auxpass
used --> ROOT
for --> prep
signature --> npadvmod
based --> amod
intrusion --> compound
detection --> pobj


In [8]:
# entity pair extraction
def get_entities(sent):
    ent1= ""
    ent2= ""
    
    prv_tok_dep = "" # dependency tag of previous token in the sentence
    prv_tok_text = "" # previous token in the sentence
    
    
    prefix = ""
    modifier= ""
    
    
    
    for tok in nlp(sent):
        
        # if token is punctuation mark, move to next token
        if tok.dep_ != "punct":
            # check: token is compound or not
            if tok.dep_ == "compound" or tok.dep_ == "acl" or tok.dep_ == "prep":
                prefix = tok.text
                # if previous word is also a compound then add the cuurrentt word to it
                if prv_tok_dep == "compound":
                    prefix  = prv_tok_text + " " + tok.text
                    #print(prefix)
                # check: token is modifier or not
            if tok.dep_.endswith("mod")== True:
                modifier = tok.text
                    # if previous word was also a compound then add the current word to it
                if prv_tok_dep == "compound":
                    modifier  = prv_tok_text + " " + tok.text
                    #print(modifier)
                
                # check: if it is a subject - entity 1
            if tok.dep_.find("subj")== True:
                ent1= modifier + " " + prefix + " " + tok.text
                #print("the first entity is:",ent1)
                prefix = ""
                modifier= ""
                prv_tok_dep = "" 
                prv_tok_text= "" 
                    
                    
                    
                    
                # check if it is an object - entity 2
            if tok.dep_.find("obj")== True:
                ent2 = ent2 + " " + modifier + " " + prefix + " " + tok.text
                prefix = ""
                modifier= ""
                #print(ent2)
                    
                # update the variables  
            prv_tok_dep = tok.dep_ 
            prv_tok_text= tok.text
                
    return [ent1.strip(), ent2.strip()]
                

In [9]:
entity_pairs=[]

for i in tqdm(data):
    entity_pairs.append(get_entities(i))

100%|██████████| 149/149 [00:01<00:00, 84.27it/s]


In [10]:
entitydf= pd.DataFrame(entity_pairs)
entitydf

0                                                  1
0                     that  unauthorized computer infrastructure   confide...
1                     that  interconnected computer systems most in domain...
2                   system                                     secure  system
3             Perpetrators                                     of cyberattack
4                     They  weaknesses  in system   them   malware   goals...
..                     ...                                                ...
144        countermeasures  laws sound without attribution  of attack  wit...
145           cyberattacks  many In countries various under laws  at cyber...
146            Attribution  of attack reasonable beyond doubt  to accused ...
147  Nations member states                   In 2021  draft cybercrime treaty
148         personal  data  breach notification laws   organizations   peo...

[149 rows x 2 columns]

In [11]:
get_entities("deep learning model will be given to students")

['deep learning model', 'students']

In [12]:
# relation extraction
# predicate is the verb in a sentence
# write a rule to get the corresponding auxiliary and the root

def get_relation(sent):
    
    doc=nlp(sent)
    
    #matcher class object
    
    matcher = Matcher(nlp.vocab)
    
    #define the pattern
    
    pattern = [ {'POS':'AUX','OP':"*"},
               {'DEP': 'ROOT'},
              {'DEP': 'prep', 'OP':"?"},
              {'DEP':'agent', 'OP':"?"},
              {'POS':'ADJ','OP':"?"}]
    
    matcher.add("matching_1", [pattern], on_match=None)
    
    matches= matcher(doc)
    #print(matches)
    #print(len(matches))
    k=len(matches)-2
    #print(k)
    span= doc[matches[k][1]:matches[k][2]]
    
    return(span.text)
    

In [13]:
get_relation("images are stored in S3 bucket")

'are stored in'

In [14]:
get_relation("Elastic application will offer cloud service")

'offer'

In [15]:
relations= [get_relation(i) for i in tqdm(data)]

100%|██████████| 149/149 [00:01<00:00, 87.74it/s]


In [16]:
pd.Series(relations).value_counts()

is          28
are         15
occur        3
See          3
have         3
            ..
build        1
may seek     1
search       1
prevent      1
began        1
Name: count, Length: 95, dtype: int64

In [17]:
relationsdf = pd.DataFrame(relations)
relationsdf.head()

0
0   occurs
1       is
2      are
3   can be
4  attempt

In [18]:
# build the Knowledge Graph
# create a dataframe of entities and relations

# extract subject
source = [i[0] for i in entity_pairs]

# extract object
target = [i[1] for i in entity_pairs]

kg_df = pd.DataFrame({'source':source, 'target':target, 'edge':relations})


In [19]:
# create a directed graph from a dataframe

G = nx.from_pandas_edgelist(kg_df, "source", "target", edge_attr=True, create_using=nx.MultiDiGraph())
#edge_labels= dict([((u,v), relations[d['weight']]) for u,v, d in G.edges(data=True)])

In [20]:
G = nx.DiGraph(directed=True)  
for i in range(len(relations)):
    G.add_weighted_edges_from([(source[i], target[i], i)])
        #print(G.nodes)
        #print(G.edges)
print("\n Knowledge Graph generated")
size =20
if (len(relations)/2)>20:
    size= len(target)/2
plt.figure(figsize=(size, size))
edge_labels= dict([((u,v), relations[d['weight']]) for u,v, d in G.edges(data=True)])
pos=nx.spring_layout(G,k=0.8)
nx.draw(G, with_labels=True, node_color='lightblue', node_size=5000, edge_color='r', edge_cmap=plt.cm.Blues, pos=pos, font_size=20)
nx.draw_networkx_edge_labels(G, pos, edge_labels= edge_labels, font_size=15)


 Knowledge Graph generated


{('that',
  'unauthorized computer infrastructure   confidentiality  of content'): Text(-0.5174345698078328, 0.1889124655223842, 'occurs'),
 ('that',
  'interconnected computer systems most in domains  of life   vulnerability  to cyberattacks   bugs   attackers'): Text(-0.29600606251426, -0.46591091146925256, 'is'),
 ('that',
  'evidence  about attack   malware  from systems   vulnerability   attack'): Text(-0.08595734930855957, -0.522675335797038, 'may attempt'),
 ('that',
  'changing Because nature  of cyberthreats   scenarios'): Text(0.016683836207314243, -0.4643730090896626, 'may produce'),
 ('that',
  'associated via companies  business relationship  with target'): Text(-0.5462942328564173, -0.13772664947427954, 'are delivered'),
 ('that',
  'as service prepacked  software   cyberattack lower as risk traditional than hacking'): Text(0.06212653187885278, 0.38585733753258933, 'is'),
 ('that',
  'also  software  used botnet   purchasers  botnets devices'): Text(-0.15948958162175497, 

In [21]:
kg_df

source                                             target  \
0                     that  unauthorized computer infrastructure   confide...   
1                     that  interconnected computer systems most in domain...   
2                   system                                     secure  system   
3             Perpetrators                                     of cyberattack   
4                     They  weaknesses  in system   them   malware   goals...   
..                     ...                                                ...   
144        countermeasures  laws sound without attribution  of attack  wit...   
145           cyberattacks  many In countries various under laws  at cyber...   
146            Attribution  of attack reasonable beyond doubt  to accused ...   
147  Nations member states                   In 2021  draft cybercrime treaty   
148         personal  data  breach notification laws   organizations   peo...   

        edge  
0     occurs  
1         is  
2        are  
3     can be  
4    attempt  
..       ...  
144  enforce  
145      are  
146       is  
147    began  
148     have  

[149 rows x 3 columns]

In [22]:
path1 = 'Raw Knowledge Graph.pkl'
joblib.dump(G, path1)
print("the graph as been saved")

path2 = "DataFrame.pkl"
joblib.dump(kg_df, path2)
print("the DataFrame has been saved")

the graph as been saved
the DataFrame has been saved
